<div>
<h1>
<center>
 <strong> <font color="teal">Quantum State Preparation Algorithm</font> </strong>
</center>
</h1>
</div>

Niels Gleinig and Torsten Hoefler in their paper <a href= "https://ieeexplore.ieee.org/document/9586240" target="_blank"> An Efficient Algorithm for Sparse Quantum State Preparation </a> show how sparsity can be leveraged to make
state preparation asymptotically more efficient than preparation of
general states.

<h2>
<center>
 <strong> <font color="grey">Mathematical statement of the algorithm</font> </strong>
</center>
</h2>


Given the set $S \subset\{0,1\}^n$ and the nonzero coefficients $c_x, x \in S$ that describe a quantum state $\phi$, find a sequence of elementary quantum gates $g_1, g_2, \ldots, g_k$, such that applying the quantum circuit $C:=g_1 g_2 \ldots g_k$ to $\left|0^n\right\rangle$ creates $C\left|0^n\right\rangle=\phi$.



Obviously, we would like the circuit $C$ to be as small as possible.<strong>
Notice that this problem is equivalent to finding a circuit $C^{\prime}:=g_1^{\prime} g_2^{\prime} \ldots g_k^{\prime}$, such that $C^{\prime} \phi=\left|0^n\right\rangle$ </strong> , because setting $C=$ $\left(g_k^{\prime}\right)^{-1}\left(g_{k-1}^{\prime}\right)^{-1} \ldots\left(g_1^{\prime}\right)^{-1}$ we have $C\left|0^n\right\rangle=\phi$. Given this direct equivalence of the problem, we can use the problem formulation that asks for finding a circuit $C$ that transforms $\phi$ to $\left|0^n\right\rangle$.

<h1>
<center>
 <strong> <font color="grey">Implementation of the algorithm in Q#</font> </strong>
</center>
</h1>

In [ ]:
# Installing qsharp
!pip install qsharp
!pip install qsharp_widgets
!pip install qsharp.estimator

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 12.4 MB/s eta 0:00:00
  Using cached jedi-0.19.1-py2.py3-none-any.whl.metadata (22 kB)
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 170.1/170.1 kB 2.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 213.7/213.7 kB 7.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 727.4/727.4 kB 19.1 MB/s eta 0:00:00
Using cached jedi-0.19.1-py2.py3-none-any.whl (1.6 MB)
ERROR: Could not find a version that satisfies the requirement qsharp.estimator (from versions: none)
ERROR: No matching distribution found for qsharp.estimator


In [ ]:
# importing necessary modules for qsharp
import numpy as np
import qsharp
from qsharp.utils import dump_operation
from qsharp_widgets import Circuit
from qsharp_widgets import SpaceChart, EstimateDetails

# Qsharp
import qsharp
from qsharp_widgets import EstimatesOverview
from qsharp.estimator import EstimatorParams, QubitParams, QECScheme

# General imports
import numpy as np
import matplotlib.pyplot as plt

In [ ]:
# Defining the Prerequisite functions

# Preparing the input for algorithm
def Preparing_input_for_algorithm(probabilities):
    S = []
    n = len(probabilities)  # Total number of elements in the list
    num_bits = n.bit_length() - 1  # Determines how many bits are needed for binary representation

    for i, amp in enumerate(probabilities):
        if amp != 0:
            # Convert the index to binary with `num_bits` length and represent it as a list of bits
            binary_index = [int(bit) for bit in format(i, f'0{num_bits}b')]
            S.append([binary_index, amp])

    return S

# This function seperate the input S into T0 and T1 where T0 and T1 are sets having most zeros and most one indices
def find_qubit_with_unequal_sets(T,n):

    best_qubit = None
    T_0=[]
    T_1=[]
    Max_difference = float('-inf')  # Initialize to negative infinity

    for b in range(n):
        # Split T into T_0 and T_1 based on qubit b
        T_0 = [x for x in T if x[0][b] == 0]
        T_1 = [x for x in T if x[0][b] == 1]

        # Check if both sets are non-empty
        if len(T_0) != 0 and len(T_1) != 0:
            difference = abs(len(T_0) - len(T_1))
            if difference > Max_difference:
                Max_difference = difference
                best_qubit = b
                best_T_0 = T_0
                best_T_1 = T_1

    return best_qubit,best_T_0, best_T_1


# This is also needed as a part of updating basis state set S in each recursion of Algo1()
def NOT(a):
  if a==0:
    return 1
  else:
    return 0

# Making list 4 adjustable for input to qsharp function
def convert_to_tuples(input_list):
  output_list = []
  for sublist in input_list:
    if len(sublist) == 3:
      sublist.insert(-1, [-1])
    output_list.append(tuple(sublist))
  return output_list

In [ ]:
# Classical part of the algorithm
def Classical_part(probabilities):

    List_1=[]    # store history of Gate types and their parameters (qubit numbering on which they are applied)
    List_2=[]    # Store X Gate history
    List_3=[]    # Store CX Gate history
    List_4=[]    # Store Multi- controlled Gate history
    List_5=[]    # Store Last step X Gates information



    S = Preparing_input_for_algorithm(probabilities)

    n=len(S[0][0])        # n is number of qubits in required Sparse State.
    n9=[]                 # list of required number of control qubits in each splitting stage

    def Algo_1():    # This is classical function called by quantum function which can create Required Gates information in Lists
      dif_qubits = []
      dif_values = []
      T = S

      # Main loop
      while len(T) > 1:
        # Find the qubit b
        P = find_qubit_with_unequal_sets(T,n)  # We already implement this logic to find the best qubit best_T_0 and best_T_1 above
        b = P[0]
        T_0 = P[1]
        T_1 = P[2]

      # Append b to dif_qubits
        dif_qubits.append(b)
        if len(T_0) < len(T_1):
          # Set T = T_0 and append 0 to dif_values
          T = T_0
          dif_values.append(0)
        else:
          # Set T = T_1 and append 1 to dif_values
          T = T_1
          dif_values.append(1)
          # Pop the last value appended to dif_qubits and store it as dif
          dif = dif_qubits.pop();
        # Pop the last value that was appended to dif_values
          dif_values.pop();
        # Store the single element in T as x_1
        x_1 = T[0]
        # T_prime subset of S denote the set of strings that have the values in dif_values on the bits dif_qubits
        T_prime = [x for x in S if all(x[0][q] == v for q, v in zip(dif_qubits, dif_values))]
        # Remove x_1 from T'
        T_prime.remove(x_1)
        # Second While loop for T_prime
        while len(T_prime) > 1:
          # Find the qubit b_prime
          R = find_qubit_with_unequal_sets(T_prime,n)  # Implement logic to find the best qubit
          b_prime = R[0]
          T_prime_0 = R[1]
          T_prime_1 = R[2]
          # Append b to dif_qubits
          dif_qubits.append(b_prime)

          if len(T_prime_0) < len(T_prime_1):
          # Set T = T_0 and append 0 to dif_values
            T_prime = T_prime_0
            dif_values.append(0)
          else:
          # Set T = T_1 and append 1 to dif_values
            T_prime = T_prime_1
            dif_values.append(1)
        x_2 = T_prime[0]

        if x_1[0][dif] != 1:
          List_1.append(1)
          List_2.append(n-1-dif)
          for x in S:
            x[0][dif]= NOT(x[0][dif])


        for b in range(n):
          if b != dif and x_1[0][b] != x_2[0][b]:
          # target b controlled on dif
            List_1.append(2)
            sx=[n-1-dif,n-1-b]
            List_3.append(sx)
            for x in S:
              if x[0][dif]==1:
                x[0][b]= NOT(x[0][b])

        for b in dif_qubits:
          if x_2[0][b] != 1:
          # not gate on line b
            List_1.append(1)
            List_2.append(n-1-b)
            for x in S:
              x[0][b]= NOT(x[0][b])

        # virtual merging operation begins

        beta = x_1[1]      # probability of x_1
        alpha = x_2[1]     #probability of x_2

        # x_1 would merge into x_2   i.e.  x2 absorb probability of x1
        x_2[1]=x_2[1]+x_1[1]
        alpha=alpha/x_2[1]
        beta=beta/x_2[1]
        List_1.append(3)

        if len(dif_qubits)>0:
          n9.append(len(dif_qubits))
          sy = [alpha,beta,dif_qubits,dif]
        else:
          sy = [alpha,beta,dif]

        List_4.append(sy)
        S.remove(x_1)
        if len(S)>1:
          Algo_1()
        else:
          List_1.append(4)
          List_5.append(x_2[0])




    if len(S)>1:
      Algo_1()


    # Extra part for checking
    # else:
    #   for b in range(0,n):
    #     if S[0][b]==1:
    #       List_1.append(5)
    #       List_6.append(x_2[0])
    #       NOT([0][b])
    #     List_1.append(4)
    #     List_5.append(S[0][0])

    List_4 = convert_to_tuples(List_4)


    return n , List_1,List_2,List_3,List_4,List_5

In [ ]:
# Quantum part of the algorithm
%%qsharp

open Microsoft.Quantum.Diagnostics;
open Microsoft.Quantum.Measurement;
open Microsoft.Quantum.Arrays;
open Microsoft.Quantum.Math;

operation Sparse_State_Algo(n:Int , List_1: Int[] , List_2:Int[] , List_3: Int[][] , List_4 : (Double,Double,Int[],Int)[] , List_5:Int[][]) : Unit {

    use q = Qubit[n];

    mutable n1 = Length(List_1);
    mutable Reversed_List_1 = List_1[Length(List_1) - 1 .. -1 .. 0];
    mutable List_2 =List_2;
    mutable List_3 =List_3;
    mutable List_4 =List_4;
    mutable List_5 =List_5;
    for i in Reversed_List_1 {

        if (i == 1)
        {
            mutable n2 = Length(List_2);
            mutable read_2 =List_2[n2-1];
            X(q[read_2]);
            set List_2 = List_2[0..Length(List_2)-2];

        }

        elif (i == 2)
        {
            mutable n3 = Length(List_3);
            mutable read_3 = List_3[n3-1];
            mutable r1 = read_3[0];
            mutable r2 = read_3[1];
            set List_3 = List_3[0..Length(List_3)-2];
            CX(q[r1],q[r2]) ;
        }

        elif (i == 3)
        {
          mutable n4 = Length(List_4);
          mutable read_4 = List_4[n4-1];
          mutable (a,b,c,d) = read_4;

          if c == [-1] {
            mutable sy1 = a;
            mutable sy2= b ;
            mutable  w = ArcTan(AbsD(sy1^0.5) / AbsD(sy2^0.5));
            mutable target = (n-1)-d;
            Ry(w,q[target]);
            X(q[target]);
            Ry(-w,q[target]);
            set List_4 = List_4[0..Length(List_4)-2];

          }

          else
          {
            mutable sy1 = a;
            mutable sy2= b ;
            mutable  w = ArcTan(AbsD(sy1^0.5) / AbsD(sy2^0.5));
            mutable target = (n-1)-d;
            let indices = c;
            mutable control = Repeated(q[0], Length(indices));
            Ry(w,q[target]);
            for idx in 0..Length(indices)-1 {
            set control w/= idx <- q[(n-1)-(indices[idx])];
            }
            Controlled X (control,q[target]);
            Ry(-w,q[target]);
            set List_4 = List_4[0..Length(List_4)-2];
          }

        }

        elif (i == 4)
        {
            mutable read_5 = List_5[0];
            mutable n5= Length(read_5);
                for b in 0..n5-1{
                    if (read_5[b]==1) {
                        X(q[(n-1)-b])}
                }
            set List_5 = List_5[0..Length(List_5)-1];

        }
        }
    Microsoft.Quantum.Diagnostics.DumpMachine();
    //let r = MeasureEachZ(q);
    ResetAll(q);
    //return r
}


### **Example 01:**
Preparing a Bell State using sparse state algorithm and estimating its resources using **Quantum Resource Estimator**.

In [ ]:
probabilities = [1/2,0,0,1/2]

In [ ]:
n, List_1 , List_2 , List_3 , List_4 , List_5 = Classical_part(probabilities)
state = qsharp.eval(f"Sparse_State_Algo({n},{List_1} ,{List_2} , {List_3}, {List_4} , {List_5})")

# Notice that we provide probability but the qashrp dump machine function shows the amplitudes by default

STATE:
|00⟩: 0.7071+0.0000𝑖
|11⟩: 0.7071+0.0000𝑖


Lets first see the circuit of the bell state prepared by the algorithm

In [ ]:
circuit = Circuit(qsharp.circuit(f"Sparse_State_Algo({n},{List_1} ,{List_2} , {List_3}, {List_4} , {List_5})"))
circuit

Circuit(circuit_json='{"operations":[{"gate":"ry","displayArgs":"0.7854","targets":[{"qId":1,"type":0}]},{"gat…

Now estimates the resources ( Uzing Azure Quantum Resource Estimator ) that the quantum computer takes to run that circuit

In [ ]:
result = qsharp.estimate(f"Sparse_State_Algo({n},{List_1} ,{List_2} , {List_3}, {List_4} , {List_5})")
estimates_overview = EstimatesOverview(result)
estimates_overview

EstimatesOverview(estimates={'status': 'success', 'jobParams': {'qecScheme': {'name': 'surface_code', 'errorCo…

Here we estimates the result using the default parameters of the **Quantum Resource Estimator**.

### **Example 02**

Estimate the resources for Bell State Circuit using customize parameters (which we learn in notebook 03)

In [ ]:
result = qsharp.estimate(f"Sparse_State_Algo({n},{List_1} ,{List_2} , {List_3}, {List_4} , {List_5})",
                         params={"errorBudget": 0.001, "qubitParams": {"name": "qubit_gate_ns_e4"}, "qecScheme": {"name": "surface_code"},"estimateType": "singlePoint"})
estimates_overview = EstimatesOverview(result)
estimates_overview

EstimatesOverview(estimates={'status': 'success', 'jobParams': {'qecScheme': {'name': 'surface_code', 'errorCo…

Note that we only change the qubits device type as our customize parameter and remain all the other factors remains same-- although here we purposely define other parametrs explicitly so you can see how we can change them as well if needs to.

### **Example 03**

Compring thr results between qubit devices:
- qubit_gate_ns_e3
- qubit_gate_ns_e4



In [ ]:
labels = ["Gate-based ns, 10⁻³", "Gate-based ns, 10⁻⁴"]
params = EstimatorParams(num_items=2)
params.error_budget = 0.001
params.items[0].qubit_params.name = QubitParams.GATE_NS_E3
params.items[0].qubit_params.estimateType = "singlePoint"
params.items[1].qubit_params.name = QubitParams.GATE_NS_E4
params.items[1].qubit_params.estimateType = "singlePoint"

result = qsharp.estimate(f"Sparse_State_Algo({n},{List_1} ,{List_2} , {List_3}, {List_4} , {List_5})", params=params)

estimates_overview = EstimatesOverview(result,runNames=labels)
estimates_overview

EstimatesOverview(estimates={0: {'status': 'success', 'jobParams': {'qecScheme': {'name': 'surface_code', 'err…

### **Task 01:**

Compring thr results between qubit devices:

- Gate-based µs, 10⁻³
- Gate-based µs, 10⁻⁴

In [ ]:
###
# Your code
###

In [ ]:
labels = ["Gate-based µs, 10⁻³", "Gate-based µs, 10⁻⁴"]
params = EstimatorParams(num_items=2)
params.error_budget = 0.01
params.items[0].qubit_params.name = QubitParams.GATE_US_E3
params.items[0].qubit_params.estimateType = "singlePoint"
params.items[1].qubit_params.name = QubitParams.GATE_US_E4
params.items[1].qubit_params.estimateType = "singlePoint"

result = qsharp.estimate(f"Sparse_State_Algo({n},{List_1} ,{List_2} , {List_3}, {List_4} , {List_5})", params=params)

estimates_overview = EstimatesOverview(result,runNames=labels)
estimates_overview

EstimatesOverview(estimates={0: {'status': 'success', 'jobParams': {'qecScheme': {'name': 'surface_code', 'err…

### **Task 02:**

Compring thr results between qubit devices:

- Majorana ns, 10⁻⁴ with floquent code
- Majorana ns, 10⁻⁶ with floquent code

In [ ]:
###
# Your code
###

In [ ]:
labels = ["Majorana ns, 10⁻⁴", "Majorana ns, 10⁻⁶"]
params = EstimatorParams(num_items=2)
params.error_budget = 0.01
params.items[0].qubit_params.name = QubitParams.MAJ_NS_E4
params.items[0].qubit_params.estimateType = "floquet_code"
params.items[1].qubit_params.name = QubitParams.MAJ_NS_E6
params.items[1].qubit_params.estimateType = "floquet_code"

result = qsharp.estimate(f"Sparse_State_Algo({n},{List_1} ,{List_2} , {List_3}, {List_4} , {List_5})", params=params)

estimates_overview = EstimatesOverview(result,runNames=labels)
estimates_overview

EstimatesOverview(estimates={0: {'status': 'success', 'jobParams': {'qecScheme': {'name': 'surface_code', 'err…

### **Task 03:**
Write a function that prepare a probability vector for a Sparse quantum state that takes three input arguments the number of qubits , number of non zero elements and how many such probabilities vector to produce in the state and outputs the corresponding sparse states and prepare that quantum states using Sparese state algorithm function.

In [ ]:
def generate_random_probabilities(n, m, num_lists):

  if m > 2**n:
      raise ValueError("m cannot be greater than the total number of possible states (2^n).")

  probabilities_lists = []

  # your code


  return probabilities_lists

In [ ]:
# Our Solution

import numpy as np

def generate_random_probabilities(n, m, num_lists):

    if m > 2**n:
      raise ValueError("m cannot be greater than the total number of possible states (2^n).")

    probabilities_lists = []

    for i in range(1, num_lists + 1):

      # Initialize the amplitude list with zeros
      amplitudes = [0] * (2**n)

      # Randomly select m positions for non-zero amplitudes
      indices = np.random.choice(range(2**n), m, replace=False)

      # Assign random complex numbers as amplitudes at the chosen indices
      for index in indices:
        amplitudes[index]= np.random.rand()

      # Normalize the amplitudes to satisfy the quantum state condition
      norm_factor = np.sqrt(sum(abs(amp)**2 for amp in amplitudes))
      normalized_amplitudes = [(amp / norm_factor)**2 for amp in amplitudes]

      probabilities_lists.append(normalized_amplitudes)

    return probabilities_lists

In [ ]:
probabilities_lists = generate_random_probabilities(2, 2, 1)
probabilities_lists

[[0.0, 0.0, 0.23602263294248949, 0.7639773670575106]]

In [ ]:
# prepare the states using Sparese_State_Alog() function

###
# Your code
###

In [ ]:
# Our Solution

n, List_1 , List_2 , List_3 , List_4 , List_5 = Classical_part(probabilities_lists[0]) # generating the first quantum state in the list
state = qsharp.eval(f"Sparse_State_Algo({n},{List_1} ,{List_2} , {List_3}, {List_4} , {List_5})")
circuit = Circuit(qsharp.circuit(f"Sparse_State_Algo({n},{List_1} ,{List_2} , {List_3}, {List_4} , {List_5})"))
circuit

STATE:
|01⟩: 0.4858+0.0000𝑖
|11⟩: 0.8741+0.0000𝑖


Circuit(circuit_json='{"operations":[{"gate":"X","targets":[{"qId":1,"type":0}]},{"gate":"ry","displayArgs":"0…

### **Task 04**:

Estimate the resources for the quantum states using Quantum resources estimator for different qubit type devices.

In [ ]:
###
# Your solution
####

In [ ]:
# Our Solution

result = qsharp.estimate(f"Sparse_State_Algo({n},{List_1} ,{List_2} , {List_3}, {List_4} , {List_5})",
    params=[
        {
            "error_budget": 0.333,
            "qubitParams": { "name": "qubit_gate_ns_e3" },
            "qecScheme": { "name": "surface_code" },
            "estimateType": "frontier", # Pareto frontier estimation
        },
        {
            "error_budget": 0.333,
            "qubitParams": { "name": "qubit_gate_ns_e4" },
            "qecScheme": { "name": "surface_code" },
            "estimateType": "frontier", # Pareto frontier estimation
        },
        {
            "error_budget": 0.333,
            "qubitParams": { "name": "qubit_gate_us_e3" },
            "qecScheme": { "name": "surface_code" },
            "estimateType": "frontier", # Pareto frontier estimation
        },
        {
            "error_budget": 0.333,
            "qubitParams": { "name": "qubit_gate_us_e4" },
            "qecScheme": { "name": "surface_code" },
            "estimateType": "frontier", # Pareto frontier estimation
        },
        {
            "error_budget": 0.333,
            "qubitParams": { "name": "qubit_maj_ns_e4" },
            "qecScheme": { "name": "surface_code" },
            "estimateType": "frontier", # Pareto frontier estimation
        },
        {
            "error_budget": 0.333,
            "qubitParams": { "name": "qubit_maj_ns_e6" },
            "qecScheme": { "name": "surface_code" },
            "estimateType": "frontier", # Pareto frontier estimation
        },
    ]
)

runNames = [
    "Gate-based µs, 10⁻³", "Gate-based µs, 10⁻⁴",
    "Gate-based ns, 10⁻³", "Gate-based ns, 10⁻⁴",
     "F-Majorana ns, 10⁻⁴", "F-Majorana ns, 10⁻⁶"
]

EstimatesOverview(result, runNames=runNames)

EstimatesOverview(estimates={0: {'status': 'success', 'jobParams': {'qecScheme': {'name': 'surface_code', 'err…